In [37]:
import numpy as np
import pandas as pd
import pickle
model = pickle.load(open('model.sav', 'rb'))
dfq = pd.read_excel('Book2samecateg.xlsx')
try:
    dfq.rename(columns={'ID': 'id'}, inplace=True)
except:
    pass
dfq.columns

Index(['title', 'Subject', 'id', 'category', 'content'], dtype='object')

In [38]:
X_train = np.load('X_train.npy')
y_train = np.load('y_train.npy')
category_id_df = pd.read_pickle('category_id_df.pkl')

from sklearn.calibration import CalibratedClassifierCV
cal_pac = CalibratedClassifierCV(base_estimator=model, cv="prefit")
cal_pac.fit(X_train, y_train)

CalibratedClassifierCV(base_estimator=PassiveAggressiveClassifier(C=10, average=False, class_weight=None,
              early_stopping=False, fit_intercept=True, loss='hinge',
              max_iter=1000, n_iter=None, n_iter_no_change=5, n_jobs=-1,
              random_state=None, shuffle=True, tol=0.0001,
              validation_fraction=0.1, verbose=0, warm_start=False),
            cv='prefit', method='sigmoid')

In [39]:
import re
import string
def clean_text_round1(text):
    #Make text lowercase, remove leading spaces
    text = text.strip().lower()
    # remove HTML tags
    text = re.sub(r'<.*?>', '', text)
    #remove text in square brackets
    text = re.sub('\[.*?\]', '', text)
    # remove the characters [\], ['] and ["]
    text = re.sub(r"\\", "", text)    
    text = re.sub(r"\'", "", text)    
    text = re.sub(r"\"", "", text) 
    #remove punctuation
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    #remove words containing numbers
    text = re.sub('\w*\d\w*', '', text)
    #Get rid of some additional punctuation
    text = re.sub('[‘’“”…]', '', text)
    #remove next line '\n'
    text = re.sub('\n', '', text)
    #remove duplicate white spaces
    text = re.sub(' +', ' ', text)
    return text
round1 = lambda x: clean_text_round1(x)

In [40]:
dfq_clean = pd.DataFrame(dfq.content.apply(round1))
dfq_temp = dfq.copy()
dfq_temp.rename(columns={'content': 'content_old'}, inplace=True)
dfq = pd.concat([dfq_temp, dfq_clean], axis=1)
dfq=dfq[dfq['content'].map(len) > 14]

with open('id_to_category.pickle', 'rb') as handle:
    id_to_category = pickle.load(handle)
df = pd.read_pickle('dt_clean.pkl')
with open('data.pickle', 'rb') as f:
    stop_words = pickle.load(f)
    
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf = TfidfVectorizer(analyzer='word', sublinear_tf=True, norm='l2', encoding='latin-1', ngram_range=(1,2), stop_words=stop_words)
tfidf_temp = tfidf.fit_transform(df.content).toarray()

cat=dfq['category'].tolist()
text=dfq['content'].tolist()
text_feature=tfidf.transform(text)
pred=model.predict(text_feature)
dfq['category_predicted']=pred

In [41]:
ds=pd.DataFrame(cal_pac.predict_proba(text_feature)*100, columns = category_id_df['category'])

In [42]:
category_predicted = []
for preditemp in pred:
    category_predicted.append(id_to_category[preditemp])
dfq['category_predicted'] = category_predicted
dfq['cat_pred=cat_orig?'] = np.where((dfq['category'] == dfq['category_predicted']), 'True', 'False')
dfq.rename(columns={'category': 'category_orignal'}, inplace=True)
dfq.rename(columns={'title': 'account_name'}, inplace=True)
dfq=dfq[['id', 'Subject', 'content_old', 'content', 'account_name', 'category_orignal', 'category_predicted', 'cat_pred=cat_orig?']]



In [43]:
dfq = pd.concat([dfq, ds], axis=1)

In [44]:
dfq=dfq.sort_values(by=['cat_pred=cat_orig?'], ascending=False)
writer = pd.ExcelWriter('output.xlsx')
dfq.to_excel(writer,'Sheet1')
writer.save()
dfq=dfq.sort_values(by=['cat_pred=cat_orig?'], ascending=False)
dfq

id                            Subject  \
0   2854035  General - Performance/Speed Issue   
11  2858111  User Interface - Date not current   
23  2860262  General - Performance/Speed Issue   
2   2854235  User Interface - Date not current   
3   2854236  User Interface - Date not current   
4   2854366                   Data Discrepancy   
5   2854461  User Interface - Date not current   
6   2854472  User Interface - Date not current   
7   2854479  User Interface - Date not current   
8   2854497                    Data Feed Issue   
9   2854515  User Interface - Date not current   
10  2857354  User Interface - Date not current   
12  2858112  User Interface - Date not current   
37  2865017  User Interface - Date not current   
13  2858113  User Interface - Date not current   
15  2858399  User Interface - Date not current   
16  2858408               Alerts - Discrepancy   
17  2858663  User Interface - Date not current   
18  2858855  User Interface - Date not current   
19  2858866  User Interface - Date not current   
20  2859460  User Interface - Date not current   
21  2859997  General - Performance/Speed Issue   
22  2860222  User Interface - Date not current   
49  2866237  User Interface - Date not current   
24  2860394               Alerts - Discrepancy   
25  2860814  General - Performance/Speed Issue   
26  2861177  User Interface - Date not current   
48  2866044  User Interface - Date not current   
27  2861378  User Interface - Date not current   
28  2862564  User Interface - Date not current   
29  2862566  User Interface - Date not current   
30  2863259  User Interface - Date not current   
31  2864708  User Interface - Date not current   
32  2864788               Alerts - Discrepancy   
33  2864791  General - Performance/Speed Issue   
34  2864814  User Interface - Date not current   
35  2864971  User Interface - Date not current   
36  2865002  User Interface - Date not current   
38  2865018  User Interface - Date not current   
1   2854234  User Interface - Date not current   
39  2865062  User Interface - Date not current   
40  2865073  User Interface - Date not current   
41  2865089  User Interface - Date not current   
42  2865116  User Interface - Date not current   
43  2865123  User Interface - Date not current   
44  2865174  User Interface - Date not current   
45  2865672  User Interface - Date not current   
46  2865832  User Interface - Date not current   
47  2865864  User Interface - Date not current   
14  2858237  User Interface - Date not current   

                                          content_old  \
0   Hello! System has not been updated since thurs...   
11  Tue 13-02-18 02:20:40 GMTClick to view system ...   
23  System is not up to date this morning and cont...   
2   Good morning I have received an "Alert" this m...   
3   Good morning I have received an "Alert" this m...   
4   Hello, due to the missing RTAV Message in the ...   
5   Hi TEam, System has been in read only mode for...   
6   I'm getting an elert that my system is not up ...   
7   The Carlyle system has been locked and in read...   
8   Processing for my property is pending completi...   
9   We are receiving the following alert. Would so...   
10  Please may I get your assistance to check on t...   
12  Tue 13-02-18 02:20:40 GMTClick to view system ...   
37  Dear Team, The system is not refreshed or upda...   
13  Tue 13-02-18 02:20:40 GMTClick to view system ...   
15  Ideas have been stuck on the update mode since...   
16  Hello IDeaS team, please see below from Infor ...   
17  The nightly inventory files submitted to the s...   
18  Dear Team, It is 10:10 am and the system is st...   
19  Dear Team, please note that I made changes to ...   
20  Hi Please review urgently as system is not up ...   
21  Dear Team, Could you kindly look into why the ...   
22  Hi All, Our system is not up to date this morn...   
49  Hello, unfortunately, for property Novotel Ham...   
24  Hi Team, Received a "System n

In [45]:
try:
    accuracy_r = (dfq.groupby(by='cat_pred=cat_orig?', as_index=False).agg({'id': pd.Series.nunique})['id'][1])*100/(len(dfq))
    print(accuracy_r,'%')
except:
    print("0% or 100%")

98.0 %


In [46]:
1

1